**1. Initial Settings and Imports**

Here is an example of a PySpark notebook to implement the Medallion architecture with Bronze, Silver, and Gold tiers, using Databricks and Delta Lake. This example follows development and performance best practices.

**Explanations:**
- Import required libraries and functions.
- Set file paths for Bronze layers   (Lakehouse)

**1. Configurações Iniciais e Importações**
Aqui está um exemplo de um notebook em PySpark para implementar a arquitetura Medallion com as camadas Bronze, Silver e Gold, utilizando Databricks e Delta Lake. Este exemplo segue as boas práticas de desenvolvimento e performance (PT-BR)

**Explicações:**
- Importar bibliotecas e funções necessárias.
- Definir os caminhos de arquivo para as camadas Bronze - (Lakehouse) - (PT-BR)

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import year, month
from pyspark.sql.functions import current_timestamp
import pandas as pd

spark = SparkSession.builder \
    .appName("Transformação Data Silver") \
    .config("spark.sql.shuffle.partitions", "200")  \
    .config("spark.sql.files.maxPartitionBytes", "128MB") \
    .config("spark.sql.parquet.compression.codec", "snappy") \
    .config("spark.sql.adaptive.enabled", "true") \
    .getOrCreate()

# Sets a fixed number of partitions to shuffle, improving parallelism
# Sets the maximum partition size to avoid too many small files
# Uses the Snappy codec for fast compression, optimizing read and write times
# Enables adaptive optimizations, adjusting the number of partitions dynamically based on data size


# Define um número fixo de partições para shuffle, melhorando o paralelismo                 
# Define o tamanho máximo de partições para evitar muitos arquivos pequenos        
# Usa o codec Snappy para compressão rápida, otimizando tempo de leitura e escrita    
# Habilita otimizações adaptativas, ajustando o número de partições dinamicamente com base no tamanho dos dados


In [0]:

# Set storage path in Bronze tier
# Definir caminho de armazenamento na camada Bronze (PT-BR)
landing_zone_path = "/mnt/lhdw/layer_landing_zone/detran2025.csv"
bronze_path = "/mnt/lhdw/layer_bronze/detran2025"

In [0]:
df_detran = spark.read.option("header", True) \
    .option("inferSchema", True) \
    .option("delimiter", ";") \
    .option("encoding", "ISO-8859-1") \
    .csv(landing_zone_path)

##adding a data_ingestion column for data control and tracking

##adicionando uma coluna data_ingestion para controle e restreamento de dados (PT-BR)

In [0]:
df_detran = df_detran.withColumn('bronze_ingestion', current_timestamp())

### Displaying the read files
### Apresentando os arquivo lido (PT-BR)

In [0]:
display(df_detran)

id data_inversa dia_semana horario uf br km municipio causa_acidente tipo_acidente classificacao_acidente fase_dia sentido_via condicao_metereologica tipo_pista tracado_via uso_solo pessoas mortos feridos_leves feridos_graves ilesos ignorados feridos veiculos latitude longitude regional delegacia uop bronze_ingestion 652493 2025-01-01 quarta-feira 2025-05-21T06:20:00.000+0000 SP 116 225 GUARULHOS Reação tardia ou ineficiente do condutor Tombamento Com Vítimas Feridas Pleno dia Decrescente Céu Claro Múltipla Reta;Declive Sim 2 0 1 0 0 1 1 2 -23,48586772 -46,54075317 SPRF-SP DEL01-SP UOP01-DEL01-SP 2025-05-21T01:24:51.834+0000 652519 2025-01-01 quarta-feira 2025-05-21T07:50:00.000+0000 CE 116 546,2 PENAFORTE Pista esburacada Colisão frontal Com Vítimas Fatais Pleno dia Crescente Céu Claro Simples Reta Não 6 1 1 0 1 4 1 6 -7,812288 -39,08333306 SPRF-CE DEL05-CE UOP03-DEL05-CE 2025-05-21T01:24:51.834+0000 652522 2025-01-01 quarta-feira 2025-05-21T08:45:00.000+0000 PR 369 88,2 CORNELIO PROCOPIO Reação tardia ou ineficiente do condutor Colisão traseira Com Vítimas Feridas Pleno dia Crescente Sol Dupla Reta;Aclive Sim 5 0 3 0 2 0 3 2 -23,182565 -50,637228 SPRF-PR DEL07-PR UOP05-DEL07-PR 2025-05-21T01:24:51.834+0000 652544 2025-01-01 quarta-feira 2025-05-21T11:00:00.000+0000 PR 116 74 CAMPINA GRANDE DO SUL Reação tardia ou ineficiente do condutor Saída de leito carroçável Com Vítimas Feridas Pleno dia Crescente Céu Claro Dupla Reta Não 5 0 1 0 4 0 1 2 -25,36517687 -49,04223028 SPRF-PR DEL01-PR UOP02-DEL01-PR 2025-05-21T01:24:51.834+0000 652549 2025-01-01 quarta-feira 2025-05-21T09:30:00.000+0000 MG 251 471 FRANCISCO SA Velocidade Incompatível Colisão frontal Com Vítimas Feridas Pleno dia Decrescente Chuva Simples Curva;Declive Não 5 0 1 1 1 2 2 4 -16,46801304 -43,43121303 SPRF-MG DEL12-MG UOP01-DEL12-MG 2025-05-21T01:24:51.834+0000 652569 2025-01-01 quarta-feira 2025-05-21T10:40:00.000+0000 MT 70 669 CACERES Transitar na contramão Colisão frontal Com Vítimas Fatais Pleno dia Crescente Céu Claro Simples Reta Não 4 2 0 0 1 2 0 5 -16,04148578 -57,25884017 SPRF-MT DEL03-MT UOP02-DEL03-MT 2025-05-21T01:24:51.834+0000 652573 2025-01-01 quarta-feira 2025-05-21T12:23:00.000+0000 RS 116 376 TAPES Ausência de reação do condutor Saída de leito carroçável Com Vítimas Feridas Pleno dia Decrescente Céu Claro Dupla Reta Não 2 0 1 0 0 1 1 2 -30,739714 -51,62594 SPRF-RS DEL02-RS UOP02-DEL02-RS 2025-05-21T01:24:51.834+0000 652617 2025-01-01 quarta-feira 2025-05-21T17:45:00.000+0000 SC 101 207,4 SAO JOSE Ausência de reação do condutor Colisão traseira Com Vítimas Feridas Pleno dia Crescente Nublado Dupla Reta Sim 2 0 1 0 1 0 1 2 -27,60001226 -48,6226467 SPRF-SC DEL01-SC UOP01-DEL01-SC 2025-05-21T01:24:51.834+0000 652625 2025-01-01 quarta-feira 2025-05-21T18:40:00.000+0000 MG 116 708,5 MURIAE Velocidade Incompatível Tombamento Com Vítimas Fatais Anoitecer Crescente Nublado Simples Curva Não 2 1 0 0 0 1 0 2 -21,16328873 -42,37968988 SPRF-MG DEL07-MG UOP02-DEL07-MG 2025-05-21T01:24:51.834+0000 652648 2025-01-01 quarta-feira 2025-05-21T17:00:00.000+0000 PE 407 7,4 AFRANIO Demais falhas mecânicas ou elétricas Incêndio Sem Vítimas Pleno dia Crescente Céu Claro Simples Aclive;Curva Não 2 0 0 0 2 0 0 1 -8,47503105 -41,0137105 SPRF-PE DEL06-PE UOP02-DEL06-PE 2025-05-21T01:24:51.834+0000 652655 2025-01-01 quarta-feira 2025-05-21T20:20:00.000+0000 SC 101 327 CAPIVARI DE BAIXO Ingestão de álcool pelo condutor Colisão com objeto Sem Vítimas Pleno dia Decrescente Garoa/Chuvisco Dupla Curva;Interseção de Vias Sim 3 0 0 0 2 1 0 3 -28,42800492 -48,88171497 SPRF-SC DEL02-SC UOP01-DEL02-SC 2025-05-21T01:24:51.834+0000 652656 2025-01-01 quarta-feira 2025-05-21T20:00:00.000+0000 MG 381 530 RIO MANSO Ausência de reação do condutor Colisão traseira Sem Vítimas Plena Noite Decrescente Chuva Dupla Curva Não 2 0 0 0 1 1 0 2 -20,17327539 -44,37545454 SPRF-MG DEL04-MG UOP03-DEL04-MG 2025-05-21T01:24:51.834+0000 652671 2025-01-01 quarta-feira 2025-05-21T21:00:00.000+0000 PB 405 51,

**2. Bronze Tier: Raw Data Ingestion**

The Bronze layer stores raw data in parquet format, without any significant transformations. Here we will simply write the raw data as parquet.

**2. Camada Bronze: Ingestão de Dados Brutos**

A camada Bronze armazena dados brutos com formato parquet, sem transformações significativas. Aqui vamos simplesmente gravar os dados brutos como parquet. (PT-BR)

In [0]:
#Write the table in Parquet format, partitioning by Year and Month of the inverse_date

# Escrever a tabela no formato Parquet, particionando por Ano e Mês da data_inversa

df_detran.withColumn("Ano", year("data_inversa")) \
         .withColumn("Mes", month("data_inversa")) \
         .write.mode("overwrite") \
         .partitionBy("Ano", "Mes") \
         .parquet(bronze_path)

### Save/Persist Data in Bronze Tier Bronze
Data will be saved in a partitioned manner **Year and Month**

### Salvar/Persistir dados na camada Bronze 
Os dados serão salvos de forma particionada **Ano e Mês**  (PT-BR)

**Justifications:**
- Reads raw data from a CSV file in the landing zone and writes that data in Parquet format to the Bronze tier.
- Parquet is chosen for its columnar support and its efficiency in terms of both space and read/write performance.

**Justificativas:**
- Lê os dados brutos a partir de um arquivo CSV na landingzone e escreve esses dados no formato Parquet na camada Bronze.
- O Parquet é escolhido pelo seu suporte a colunas e sua eficiência tanto em termos de espaço quanto em desempenho de leitura e escrita. (PT-BR)

**Evidence from data in the bronze layer partitioned by year and month**

**Evidência dos dados na camada bronze particionado por  ano e mês** (PT-BR)

In [0]:
%fs ls /mnt/lhdw/layer_bronze/detran2025

path name size modificationTime dbfs:/mnt/lhdw/layer_bronze/detran2025/Ano=2025/ Ano=2025/ 0 0 dbfs:/mnt/lhdw/layer_bronze/detran2025/_SUCCESS _SUCCESS 0 1747790708000 dbfs:/mnt/lhdw/layer_bronze/detran2025/_committed_4640736340123013664 _committed_4640736340123013664 35 1747578339000

### Manage memory usage
In PySpark, it is important to manage memory usage efficiently, especially when working with large datasets. To do this, you can use some specific commands that help you free up memory, remove cached or persisted objects, and force garbage collection.

### Gerenciar o uso de memória 
Em PySpark, é importante gerenciar o uso de memória eficientemente, especialmente quando se trabalha com grandes conjuntos de dados. Para isso, você pode usar alguns comandos específicos que ajudam a liberar memória, remover objetos em cache ou persistidos e forçar a coleta de lixo. (PT-BR)

In [0]:
#Clear Cache: PySpark caches data to improve the performance of repeated operations. To release this data, you can use the unpersist() command.

#Limpar cache: PySpark armazena dados em cache para melhorar o desempenho de operações repetidas. Para liberar esses dados, você pode usar o comando unpersist(). (PT-BR)

# Example of how to flush the cache of a DataFrame
# Exemplo de como liberar o cache de um DataFrame (PT-BR)

df_detran.unpersist()

# The unpersist() command removes the DataFrame from the cache, freeing up the associated memory. It is especially useful when you no longer need the persisted data.

# O comando unpersist() remove o DataFrame do cache, liberando a memória associada. Ele é especialmente útil quando você já não precisa mais dos dados persistidos. (PT-BR)

Out[7]: DataFrame[id: int, data_inversa: date, dia_semana: string, horario: timestamp, uf: string, br: int, km: string, municipio: string, causa_acidente: string, tipo_acidente: string, classificacao_acidente: string, fase_dia: string, sentido_via: string, condicao_metereologica: string, tipo_pista: string, tracado_via: string, uso_solo: string, pessoas: int, mortos: int, feridos_leves: int, feridos_graves: int, ilesos: int, ignorados: int, feridos: int, veiculos: int, latitude: string, longitude: string, regional: string, delegacia: string, uop: string, bronze_ingestion: timestamp]

**3. Clear all cached data:**
If there are multiple DataFrames in the cache, you can clear them all at once.

**3. Limpar todos os dados em cache:**
Se houver vários DataFrames em cache, você pode limpá-los todos de uma vez. (PT-BR)

In [0]:
# Clear all cached data

#Limpar todos os dados em cache (PT-BR)

spark.catalog.clearCache()

# clearCache() clears the cache of all cached objects in the current SparkSession, freeing up a significant amount of memory when multiple DataFrames are being reused.

# clearCache() limpa o cache de todos os objetos em cache no SparkSession atual, liberando uma quantidade significativa de memória quando múltiplos DataFrames estão sendo reutilizados. (PT-BR)

**4. Force Garbage Collection:**
Python has a garbage collector that removes unreferenced objects from memory. You can force garbage collection to free up memory.

**4. Forçar coleta de lixo:**
O Python possui um coletor de lixo que remove objetos não referenciados da memória. Você pode forçar a coleta de lixo para liberar memória.(PT-BR)

In [0]:
import gc
gc.collect()

#Comment: This command forces the garbage collector to run immediately, freeing up memory from Python objects that are no longer in use.

#Comentário: Esse comando força o coletor de lixo a executar imediatamente, liberando a memória de objetos Python que não estão mais em uso.(PT-BR)

Out[9]: 490

**5. Manually release variables:**
If you have created large variables that are no longer needed, you can explicitly remove them.

**5. Liberar variáveis manualmente:**
Se você criou variáveis grandes que não são mais necessárias, você pode removê-las explicitamente.(PT-BR)

In [0]:
del df_detran
# The del command removes the object from memory. This is useful when you have large DataFrames or Python objects that are no longer needed.

# O comando del remove o objeto da memória. Isso é útil quando você tem grandes DataFrames ou objetos Python que já não são necessários.(PT-BR)

%md

**Additional tips:**
- Avoid caching unnecessary DataFrames.

**Dicas adicionais:**
- Evite cachear DataFrames desnecessários. (PT-BR)
